# Atelier DAY 2

Dans ce notebook, nous reprenons les données travaillées dans l'atelier Day 1 pour tester les algorithmes de machine leraning

- gradient boosting machine 
- random forest

Les données sont 

- pour le problème de score sur données *classiques* : 
    - `df_brut`
    - `df_dum`
    - `df_dumN`
    - `df_dumAll`
- pour le problème de classification sur données *texte*
    - `imdb_cod`
    - `imdb_occ`
    
# Table des matières

[1. Préliminaires ](#basics)<br>
[2. Modélisations ](#model)<br>
[3. Performance](#perf)<br>

<a id='basics'></a>
# 1. Préliminaires 

In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

path_data = './'
path_travail = './'

## Split des données 

Avec le même taux de cible : base LEARN = 70% et base test = 30%

In [ ]:
import os
import pickle as pkl
from sklearn.model_selection import train_test_split

# Chargement base de travail
with open(os.path.join(path_travail, 'df_brut.pkl'), 'rb') as f:
    data = pkl.load(f)
    
X, y = data['features'], data['labels']
features_names = X.columns.tolist()

# split TRAIN/TEST

X_train, X_test, y_train, y_test = train_test_split(X, y, # stratify=y, 
                                                    test_size=0.3, random_state=15)

<a id='model'></a>
# 2. Modélisations

Nous proposons trois modélisations possibles :
- xgboost
- lightgbm
- RandomForestClassifier

## Modélisation XGBOOST

In [ ]:
# Modelisation XGBOOST

import xgboost as xgb

params = {
    'objective': 'binary:logistic',
    'n_estimators': 500, 
    'colsample_bytree': 0.3,
    'learning_rate': 0.05,
    'max_depth': 3
}

# creation du model
xgbo = xgb.XGBRegressor(params=params)
# apprentissage
xgbo.fit(X_train, y_train)

In [ ]:
X_train.info() 

In [ ]:
cols =  X_train.select_dtypes(exclude=['float']).columns
temp1 = X_train[cols].apply(pd.to_numeric, downcast='float', errors='coerce')
cols =  X_train.select_dtypes(include=['float']).columns
temp2 = X_train[cols]
X_train = pd.concat([temp2,temp1], axis=1)

cols =  X_test.select_dtypes(exclude=['float']).columns
temp1 = X_test[cols].apply(pd.to_numeric, downcast='float', errors='coerce')
cols =  X_test.select_dtypes(include=['float']).columns
temp2 = X_test[cols]
X_test = pd.concat([temp2,temp1], axis=1)

X_train.head()

In [ ]:
# Modelisation XGBOOST
from sklearn.metrics import auc, roc_curve

params = {
    'objective': 'binary:logistic',
    'n_estimators': 500, 
    'colsample_bytree': 0.3,
    'learning_rate': 0.05,
    'max_depth': 3,
    'eval_metric' : 'auc'
}

# creation du model
xgbo = xgb.XGBRegressor(params=params)
print(xgb)
# apprentissage
xgbo.fit(X_train,y_train)
# reapplication
pred_XGB = xgbo.predict(X_test)

fpr, tpr, _ = roc_curve(y_test, pred_XGB )
print('AUC XGBOOST =', auc(fpr, tpr))

In [ ]:
xgb.plot_importance(xgbo)

## Modélisation LightGBM

In [ ]:
# Modelisation LightGBM
import lightgbm as lgb

# Creation du modele
lgbm = lgb.LGBMRegressor(objective='binary',
                        num_leaves=21,
                        learning_rate=0.05,
                        feature_fraction = 0.2,
                        bagging_fraction = 1,
                        n_estimators=100)

# apprentissage
lgbm.fit(X_train,y_train)
# reapplication
pred_LGBM = lgbm.predict(X_test)

fpr, tpr, _ = roc_curve(y_test, pred_LGBM )
print('AUC LGBM =', auc(fpr, tpr))

In [ ]:
# Importance des variables explicatives
var_importance = lgbm.feature_importances_
var_importance = 100.0 * (var_importance / var_importance.sum())
sorted_idx = np.argsort(var_importance)
pos = np.arange(sorted_idx.shape[0]) + .5

plt.figure(figsize=(15, 6))
plt.barh(pos, var_importance[sorted_idx], align='center')
plt.yticks(pos, X_train.columns[sorted_idx])
plt.xlabel('Relative Importance')
plt.title('Variable Importance')
plt.show()

##  Modélisation Random Forest



In [ ]:
# Modelisation Random Forest
from sklearn import ensemble
from sklearn.ensemble import RandomForestClassifier


#creation du modele
rf = RandomForestClassifier(
    n_estimators=100, # Nombre d'arbres
    max_features=0.7, # à chaque split. c'est en % de p. par defaut sqrt(p),
    max_depth=12,      # complexité
    random_state=2,
    oob_score=True,
    criterion='gini'
)
# apprentissage
rf.fit(X_train, y_train)
# reapplication
pred_RF = rf.predict(X_test)
pred_RF2 = rf.predict_proba(X_test)[:,1]

fpr, tpr, _ = roc_curve(y_test, pred_RF2 )
print('AUC RF =', auc(fpr, tpr))

# 3. Performances

In [ ]:
from sklearn.metrics import roc_curve, auc, precision_recall_curve, f1_score

# Performance ROC pour les différentes stratégies sur TEST
plt.figure(figsize=(7, 6))
plt.plot([0, 1], [0, 1], 'k--')

fpr, tpr, _ = roc_curve(y_test, pred_XGB )
plt.plot(fpr, tpr, label="Data Brut XGboost (AUC=%.2f)" % auc(fpr, tpr), lw=2)
plt.legend(loc="lower right", fontsize=10)

plt.xlim([0.0, 1.0])
plt.ylim([0.0, 1.05])
plt.xlabel('False Positive Rate', fontsize=16)
plt.ylabel('True Positive Rate', fontsize=16)
plt.title('Receiver operating characteristic', fontsize=18)
plt.legend(loc="lower right", fontsize=10)

fpr, tpr, _ = roc_curve(y_test, pred_LGBM)
plt.plot(fpr, tpr, label="Data Brut LightGBM (AUC=%.2f)" % auc(fpr, tpr), lw=2)
plt.legend(loc="lower right", fontsize=10)

fpr, tpr, _ = roc_curve(y_test, pred_RF2)
plt.plot(fpr, tpr, label="Data Brut RF (AUC=%.2f)" % auc(fpr, tpr), lw=2)
plt.legend(loc="lower right", fontsize=10)

In [ ]:
# Attention, un peu long a tourner!
# discute du choix du nombre d'arbres
from collections import OrderedDict

ensemble_rf = [
    ("RandomForestClassifier, max_features='sqrt'",
     RandomForestClassifier(max_features="sqrt", oob_score=True, random_state=0)),
    ("RandomForestClassifier, max_features=None", 
     RandomForestClassifier(max_features=None, oob_score=True, random_state=0))
]

# Formatage du tableau des erreurs 
err = OrderedDict((typ, []) for typ, _ in ensemble_rf)

# Rang du nombre d'arbres 
min_estimators = 20
max_estimators = 100

for typ, rf in ensemble_rf:
    for i in range(min_estimators, max_estimators + 1, 10):
        rf.set_params(n_estimators=i)
        rf.fit(X_train, y_train)
        oob_err = 1 - rf.oob_score_
        err[typ].append((i, oob_err))

# les "OOB taux d'erreur" en fonction de "n_estimators" 
for typ, rf_err in err.items():
    xs, ys = zip(*rf_err)
    plt.plot(xs, ys, label=typ)
    
plt.xlim(min_estimators, max_estimators)
plt.xlabel("n_estimators")
plt.ylabel("OOB taux erreur")
plt.legend(loc="upper right")
plt.show()

### Exercice 

Chercher un "meilleur" modèle pour chacune des bases 
- `df_dum`
- `df_dumN`
- `df_dumAll`
- `imdb_cod`
- `imdb_occ`



# Classification sur données textuelles

Nous reprenons les tables de travail dans lesquelles les données sont codées en considérant les occurences de mots.

## Chargement

In [ ]:
# Chargement base de travail
with open(os.path.join(path_travail, 'imdb_train_occ.pkl'), 'rb') as f:
    data = pkl.load(f)
    
X_train, y_train = data['features'], data['labels']

with open(os.path.join(path_travail, 'imdb_test_occ.pkl'), 'rb') as f:
    data = pkl.load(f)
    
X_test, y_test = data['features'], data['labels']

## Modélisations

De manière à tracer une courbe ROC pour évaluer les performances, nous allons résoudre un problème de score sur les données IMDB. L'affectation aux classes "Positif"/"Négatif" se fera 'à la main'.

In [ ]:
############################
params = {
    'objective': 'binary:logistic',
    'n_estimators': 50, 
    'colsample_bytree': 0.3,
    'learning_rate': 0.05,
    'max_depth': 3,
    'eval_metric' : 'auc'
}
xgbo = xgb.XGBRegressor(params=params)
xgbo.fit(X_train,y_train)
pred_XGB = xgbo.predict(X_test)

############################
lgbm = lgb.LGBMRegressor(objective='binary',
                        num_leaves=21,
                        learning_rate=0.05,
                        feature_fraction = 0.2,
                        bagging_fraction = 1,
                        n_estimators=50)
lgbm.fit(X_train,y_train)
pred_LGBM = lgbm.predict(X_test)

############################
rf = RandomForestClassifier(
    n_estimators=50, # Nombre d'arbres
    max_features=0.9, # à chaque split. c'est en % de p. par defaut sqrt(p),
    max_depth=6,      # complexité
    random_state=2,
    oob_score=True,
    criterion='entropy'
)
rf.fit(X_train, y_train)
pred_RF = rf.predict_proba(X_test)[:,1]

## Performances

In [ ]:
from sklearn.metrics import roc_curve, auc, precision_recall_curve, f1_score

# Performance ROC pour les différentes stratégies sur TEST

plt.figure(figsize=(7, 6))
plt.plot([0, 1], [0, 1], 'k--')

fpr, tpr, _ = roc_curve(y_test, pred_XGB )
plt.plot(fpr, tpr, label="Data Occ XGboost (AUC=%.2f)" % auc(fpr, tpr), lw=2)
plt.legend(loc="lower right", fontsize=10)

plt.xlim([0.0, 1.0])
plt.ylim([0.0, 1.05])
plt.xlabel('False Positive Rate', fontsize=16)
plt.ylabel('True Positive Rate', fontsize=16)
plt.title('Receiver operating characteristic', fontsize=18)
plt.legend(loc="lower right", fontsize=10)

fpr, tpr, _ = roc_curve(y_test, pred_LGBM)
plt.plot(fpr, tpr, label="Data Occ LightGBM (AUC=%.2f)" % auc(fpr, tpr), lw=2)
plt.legend(loc="lower right", fontsize=10)

fpr, tpr, _ = roc_curve(y_test, pred_RF)
plt.plot(fpr, tpr, label="Data Occ RF (AUC=%.2f)" % auc(fpr, tpr), lw=2)
plt.legend(loc="lower right", fontsize=10)

In [ ]:
from sklearn.metrics import classification_report, confusion_matrix

seuil = 0.5
print("Performances RF")
temp = pd.Series(pred_RF).copy()
temp[pred_RF < seuil] = 0
temp[pred_RF > seuil] = 1
print(classification_report(y_test, temp))
print(confusion_matrix(y_test, temp))

print("\nPerformances LGBM")
temp = pd.Series(pred_LGBM).copy()
temp[pred_LGBM < seuil] = 0
temp[pred_LGBM > seuil] = 1
print(classification_report(y_test, temp))
print(confusion_matrix(y_test, temp))

print("\nPerformances XGB")
temp = pd.Series(pred_XGB).copy()
temp[pred_XGB < seuil] = 0
temp[pred_XGB > seuil] = 1
print(classification_report(y_test, temp))
print(confusion_matrix(y_test, temp))

### Idée : 
- faire varier le seuil selon l'objectif désiré